In [1]:
import numpy as np
import pandas as pd
from copy import copy
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.preprocessing import OneHotEncoder, MultiLabelBinarizer
from sklearn.impute import SimpleImputer 
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score, hamming_loss
import matplotlib.pyplot as plt
from sklearn.metrics import classification_report
import wandb

In [13]:
data = pd.read_csv('WineQT.csv', header=0)

In [14]:
train_data, temp_data = train_test_split(data, test_size=0.4,random_state = 42)
validation_data, test_data = train_test_split(temp_data, test_size=0.5, random_state = 42)

In [15]:
scaler = StandardScaler()
minmax_scaler = MinMaxScaler()

# Fit and transform on the training data
imputer = SimpleImputer(strategy='mean')  # You can choose 'mean', 'median', or other strategies

# Fit and transform on the training data
train_data_scaled = scaler.fit_transform(imputer.fit_transform(train_data.drop(columns=['quality'])))
train_labels = train_data['quality']

# Transform the validation and test data using the same scalers and imputer
validation_data_scaled = scaler.transform(imputer.transform(validation_data.drop(columns=['quality'])))
test_data_scaled = scaler.transform(imputer.transform(test_data.drop(columns=['quality'])))

# If you also want to normalize the data, you can do it using the MinMaxScaler
train_data_scaled_normalized = minmax_scaler.fit_transform(train_data_scaled)
validation_data_scaled_normalized = minmax_scaler.transform(validation_data_scaled)
test_data_scaled_normalized = minmax_scaler.transform(test_data_scaled)

# print(train_labels)
# print(train_data_scaled_normalized)
# print(test_data_scaled_normalized.shape)
# print(validation_data_scaled_normalized.shape)
X_train = train_data_scaled
y_train = train_labels
X_val = validation_data_scaled
y_val = validation_data['quality']
X_test = test_data_scaled
y_test = validation_data['quality']
y_train = np.array(y_train)
# y_val = np.array(y_val)
y_val = pd.get_dummies(y_val).astype(int)
y_val = np.array(y_val)
y_train = pd.get_dummies(y_train).astype(int)
y_train = np.array(y_train)
y_test = pd.get_dummies(y_test).astype(int)
y_test = np.array(y_test)
print(X_train)
print(y_train)


[[-1.67058247  1.20622441 -0.91067852 ... -0.59135112  1.0674252
   1.64361099]
 [-0.548498    0.69262724 -1.37982978 ... -1.11462937 -0.42042679
  -1.73858966]
 [-0.0169843   1.14915806 -0.28514351 ... -0.82391923 -0.88538054
  -0.31652802]
 ...
 [-0.48944092 -1.01936335  0.3403915  ... -0.358783    1.34639745
   1.62012349]
 [-0.19415553  0.23609641  0.23613566 ...  0.16449526 -0.88538054
   0.84290061]
 [-0.43038384 -0.04923535  0.70528692 ... -0.12621489  1.2534067
   1.60944735]]
[[0 0 0 1 0 0]
 [0 0 0 0 1 0]
 [0 0 1 0 0 0]
 ...
 [0 0 0 1 0 0]
 [0 0 0 1 0 0]
 [0 0 0 1 0 0]]


In [16]:
# class Neural_Network(object):
#     def __init__(self, learning_rate=0.01,epochs = 5000, inputLayerSize: int = 2, hiddenLayerSize: int = 3, outputLayerSize: int = 1):
#         # Define Hyperparameters
#         self.inputLayerSize = inputLayerSize
#         self.outputLayerSize = outputLayerSize
#         self.hiddenLayerSize = hiddenLayerSize
#         self.activation = self.relu
#         self.activationPrime = self.reluPrime
#         self.learning_rate = learning_rate
#         # Weights (parameters)
#         self.W1 = np.random.randn(self.inputLayerSize, self.hiddenLayerSize)
#         self.W2 = np.random.randn(self.hiddenLayerSize, self.outputLayerSize)
#         self.optimizer = 'SGD'
#         self.max_iterations = epochs

#     def forward(self, X):
#         self.z2 = np.dot(X, self.W1)
#         self.a2 = self.activation(self.z2)  # Use ReLU activation function
#         self.z3 = np.dot(self.a2, self.W2)
#         yHat = self.softmax(self.z3)
#         return yHat

#     def relu(self, z):
#         return np.maximum(0, z)  # ReLU activation

#     def tanh(self, z):
#         return np.tanh(z)  # Tanh activation

#     def sigmoid(self, z):
#         return 1 / (1 + np.exp(-z))

#     def sigmoidPrime(self, z):
#         return np.exp(-z) / ((1 + np.exp(-z))**2)

#     def softmax(self, z):
#         exp_z = np.exp(z - np.max(z))  # Subtracting max(z) for numerical stability
#         return exp_z / exp_z.sum(axis=1, keepdims=True)

#     def costFunction(self, X, y):
#         self.yHat = self.forward(X)
#         J = -np.sum(y * np.log(self.yHat)) / len(X)
#         return J

#     def costFunctionPrime(self, X, y):
#         self.yHat = self.forward(X)

#         delta3 = self.yHat - y
#         dJdW2 = np.dot(self.a2.T, delta3)

#         delta2 = np.dot(delta3, self.W2.T) * self.activationPrime(self.z2)  # Use ReLU derivative
#         dJdW1 = np.dot(X.T, delta2)

#         return dJdW1, dJdW2

#     def reluPrime(self, z):
#         return np.where(z > 0, 1, 0)  # Derivative of ReLU

#     def tanhPrime(self, z):
#         return 1 - np.tanh(z)**2  # Derivative of Tanh

#     def backward(self, X, y, learning_rate):
#         dJdW1, dJdW2 = self.costFunctionPrime(X, y)
#         self.W1 -= learning_rate * dJdW1
#         self.W2 -= learning_rate * dJdW2
#     def train(self, X, y, batch_size = 32, learning_rate=0.1, max_iterations=10000):
#         if(self.optimizer == 'SGD'):
#             return self.train_sgd(X=X, y=y)
#         elif(self.optimizer == 'Batch'):
#             return self.train_batch(X=X, y=y)
#         elif(self.optimizer == 'MiniBatch'):
#             return self.train_mini_batch(X=X, y=y)
#     def train_sgd(self, X, y, learning_rate=0.1, max_iterations=10000):
#         for i in range(self.max_iterations):
#             idx = np.random.randint(len(X))
#             self.backward(X[idx:idx+1], y[idx:idx+1], learning_rate)
#             # if i % 1000 == 0:
#             #     loss = self.costFunction(X, y)
#             #     print("Iteration %d: loss = %f" % (i, loss))
#         loss = self.costFunction(X, y)
#         return loss
#         print("Training completed.")
#     def train_batch(self, X, y, learning_rate=0.0001, max_iterations=10000):
#         for i in range(self.max_iterations):
#             self.backward(X, y, learning_rate)
#             # if i % 1000 == 0:
#             #     loss = self.costFunction(X, y)
#             #     print("Iteration %d: loss = %f" % (i, loss))
#         loss = self.costFunction(X, y)
#         return loss
#         print("Training completed.")
#     def train_mini_batch(self, X, y, batch_size=32, learning_rate=0.01, max_iterations=5000):
#         for i in range(self.max_iterations):
#             # Randomly shuffle the data and split into mini-batches
#             indices = np.arange(len(X))
#             np.random.shuffle(indices)
#             for j in range(0, len(X), batch_size):
#                 batch_indices = indices[j:j+batch_size]
#                 self.backward(X[batch_indices], y[batch_indices], learning_rate)
#             if i % 1 == 0:
#                 loss = self.costFunction(X, y)
#                 print("Iteration %d: loss = %f" % (i, loss))
#         loss = self.costFunction(X, y)
#         return loss
#         print("Training completed.")

#     def predict(self, X):
#         yHat = self.forward(X)
#         # return yHat
#         binary_predictions = np.zeros_like(yHat)
#         binary_predictions[np.arange(len(yHat)), yHat.argmax(axis=1)] = 1
#         return binary_predictions
#         # return np.argmax(yHat, axis=1)
#     def set_learning_rate(self, learning_rate):
#         self.learning_rate = learning_rate

#     def set_activation_function(self, activation_function):
#         if(activation_function == 'sigmoid'):
#             self.activation = self.sigmoid
#             self.activationPrime = self.sigmoidPrime
#         if(activation_function == 'relu'):
#             self.activation = self.relu
#             self.activationPrime = self.reluPrime
#         if(activation_function == 'tanh'):
#             self.activation = self.tanh
#             self.activationPrime = self.tanhPrime

#     def set_optimizer(self, optimizer):
#         self.optimizer = optimizer

#     def set_hidden_layers(self, hidden_layer_sizes):
#         self.hidden_layer_sizes = hidden_layer_sizes
#         self.W1 = np.random.randn(self.inputLayerSize, self.hiddenLayerSize)
#         self.W2 = np.random.randn(self.hiddenLayerSize, self.outputLayerSize)
#         # self.weights, self.biases = self.initialize_weights()
#     def set_epochs(self, epcohs):
#         self.max_iterations = epochs
#         print(self.max_iterations)


In [17]:
class Neural_Network(object):
    def __init__(self, learning_rate=0.01,epochs = 5000, inputLayerSize: int = 2, hiddenLayerSize = [3,3,3] , outputLayerSize: int = 1):
        # Define Hyperparameters
        self.inputLayerSize = inputLayerSize
        self.outputLayerSize = outputLayerSize
        self.hiddenLayerSize = hiddenLayerSize
        self.activation = self.relu
        self.activationPrime = self.reluPrime
        self.learning_rate = learning_rate
        # Weights (parameters)
        self.num_layers = len(hiddenLayerSize)+1
        self.weights = []
        self.weights.append(np.random.randn(self.inputLayerSize, self.hiddenLayerSize[0]))
        for i in range(1,self.num_layers-1):
            self.weights.append(np.random.randn(self.hiddenLayerSize[i-1], self.hiddenLayerSize[i]))
        self.weights.append(np.random.randn(self.hiddenLayerSize[-1], self.outputLayerSize))
        self.optimizer = 'SGD'
        self.max_iterations = epochs

    def forward(self, X):
        self.z = [None] * (len(self.weights))
        self.a = [None] * (len(self.weights)-1)
        
        self.z[0] = np.dot(X, self.weights[0])
        for i in range(0,len(self.a)):
            self.a[i] = self.activation(self.z[i])
            self.z[i+1] = np.dot(self.a[i],self.weights[i+1])
        yHat = self.softmax(self.z[-1])
        return yHat

    def relu(self, z):
        return np.maximum(0, z)  # ReLU activation

    def tanh(self, z):
        return np.tanh(z)  # Tanh activation

    def sigmoid(self, z):
        return 1 / (1 + np.exp(-z))

    def sigmoidPrime(self, z):
        return np.exp(-z) / ((1 + np.exp(-z))**2)

    def softmax(self, z):
        exp_z = np.exp(z - np.max(z))  # Subtracting max(z) for numerical stability
        return exp_z / exp_z.sum(axis=1, keepdims=True)

    def costFunction(self, X, y):
        self.yHat = self.forward(X)
        J = -np.sum(y * np.log(self.yHat)) / len(X)
        return J

    def costFunctionPrime(self, X, y):
        self.yHat = self.forward(X)
        deltas = [None] * (len(self.weights))
        deltas[-1] = self.yHat - y
        dJdWs = [None] * (len(self.weights))
        for i in range(len(deltas)-2,-1,-1):
            dJdWs[i+1] = np.dot(self.a[i].T, deltas[i+1])
            deltas[i] = np.dot(deltas[i+1],self.weights[i+1].T)*self.activationPrime(self.z[i])
        dJdWs[0] = np.dot(X.T, deltas[0])
        
        # delta3 = self.yHat - y
        # dJdW2 = np.dot(self.a2.T, delta3)

        # delta2 = np.dot(delta3, self.W2.T) * self.activationPrime(self.z2)  # Use ReLU derivative
        # dJdW1 = np.dot(X.T, delta2)

        return dJdWs

    def reluPrime(self, z):
        return np.where(z > 0, 1, 0)  # Derivative of ReLU

    def tanhPrime(self, z):
        return 1 - np.tanh(z)**2  # Derivative of Tanh

    def backward(self, X, y, learning_rate):
        dJdWs = self.costFunctionPrime(X, y)
        for i in range(len(self.weights)):
            self.weights[i] -= learning_rate * dJdWs[i]
        # self.W1 -= learning_rate * dJdW1
        # self.W2 -= learning_rate * dJdW2
    def train(self, X, y, batch_size = 32, learning_rate=0.1, max_iterations=10000):
        if(self.optimizer == 'SGD'):
            return self.train_sgd(X=X, y=y)
        elif(self.optimizer == 'Batch'):
            return self.train_batch(X=X, y=y)
        elif(self.optimizer == 'MiniBatch'):
            return self.train_mini_batch(X=X, y=y)
    def train_sgd(self, X, y, learning_rate=0.1, max_iterations=10000):
        for i in range(self.max_iterations):
            idx = np.random.randint(len(X))
            self.backward(X[idx:idx+1], y[idx:idx+1], learning_rate)
            # if i % 1000 == 0:
            #     loss = self.costFunction(X, y)
            #     print("Iteration %d: loss = %f" % (i, loss))
        loss = self.costFunction(X, y)
        return loss
        print("Training completed.")
    def train_batch(self, X, y, learning_rate=0.0001, max_iterations=10000):
        for i in range(self.max_iterations):
            self.backward(X, y, learning_rate)
            # if i % 1000 == 0:
            #     loss = self.costFunction(X, y)
            #     print("Iteration %d: loss = %f" % (i, loss))
        loss = self.costFunction(X, y)
        return loss
        print("Training completed.")
    def train_mini_batch(self, X, y, batch_size=32, learning_rate=0.01, max_iterations=5000):
        for i in range(self.max_iterations):
            # Randomly shuffle the data and split into mini-batches
            indices = np.arange(len(X))
            np.random.shuffle(indices)
            for j in range(0, len(X), batch_size):
                batch_indices = indices[j:j+batch_size]
                self.backward(X[batch_indices], y[batch_indices], learning_rate)
            if i % 1 == 0:
                loss = self.costFunction(X, y)
                print("Iteration %d: loss = %f" % (i, loss))
        loss = self.costFunction(X, y)
        return loss
        print("Training completed.")

    def predict(self, X):
        yHat = self.forward(X)
        # return yHat
        binary_predictions = np.zeros_like(yHat)
        binary_predictions[np.arange(len(yHat)), yHat.argmax(axis=1)] = 1
        return binary_predictions
        # return np.argmax(yHat, axis=1)
    def set_learning_rate(self, learning_rate):
        self.learning_rate = learning_rate

    def set_activation_function(self, activation_function):
        if(activation_function == 'sigmoid'):
            self.activation = self.sigmoid
            self.activationPrime = self.sigmoidPrime
        if(activation_function == 'relu'):
            self.activation = self.relu
            self.activationPrime = self.reluPrime
        if(activation_function == 'tanh'):
            self.activation = self.tanh
            self.activationPrime = self.tanhPrime

    def set_optimizer(self, optimizer):
        self.optimizer = optimizer

    def set_hidden_layers(self, hidden_layer_sizes):
        self.hiddenLayerSize = hidden_layer_sizes
        self.num_layers = len(self.hiddenLayerSize)+1
        self.weights = []
        self.weights.append(np.random.randn(self.inputLayerSize, self.hiddenLayerSize[0]))
        for i in range(1,self.num_layers-1):
            self.weights.append(np.random.randn(self.hiddenLayerSize[i-1], self.hiddenLayerSize[i]))
        self.weights.append(np.random.randn(self.hiddenLayerSize[-1], self.outputLayerSize))
        # self.W1 = np.random.randn(self.inputLayerSize, self.hiddenLayerSize)
        # self.W2 = np.random.randn(self.hiddenLayerSize, self.outputLayerSize)
        # self.weights, self.biases = self.initialize_weights()
    def set_epochs(self, epcohs):
        self.max_iterations = epochs
        print(self.max_iterations)


In [18]:
wandb.login()

wandb: Currently logged in as: lsamourya07 (mourya). Use `wandb login --relogin` to force relogin


True

In [19]:
wandb.init(project="MLP Classification on WineQT.csv")
np.random.seed(27)
mlp_sgd = Neural_Network(learning_rate=0.01,epochs=5000, inputLayerSize=12, hiddenLayerSize=[18], outputLayerSize=6)
mlp_sgd.set_activation_function('relu')
mlp_sgd.set_optimizer('MiniBatch')
loss = mlp_sgd.train(X_train, y_train)
y_pred = mlp_sgd.predict(X_val)
acc = accuracy_score(y_val, y_pred)
f1 = f1_score(y_val, y_pred, average='macro') 
precision = precision_score(y_val, y_pred, average='macro')
recall = recall_score(y_val, y_pred, average='macro')
print("Loss:", loss)
print("Accuracy:", acc)
print("F1 Score:", f1)
print("Precision:", precision)
print("Recall:", recall)
y_train_pred = mlp_sgd.predict(X_train)
train_accuracy = accuracy_score(y_train, y_train_pred)
train_f1 = f1_score(y_train, y_train_pred, average='macro')  
train_precision = precision_score(y_train, y_train_pred, average='macro')
train_recall = recall_score(y_train, y_train_pred, average='macro')
print("Loss:", loss)
print("Accuracy:", train_accuracy)
print("F1 Score:", train_f1)
print("Precision:", train_precision)
print("Recall:", train_recall)
print(acc)
print(train_accuracy)
wandb.log({"Loss": loss, "Accuracy": acc})
wandb.log({"Loss": loss, "Accuracy": train_accuracy})

Iteration 0: loss = 2.077601
Iteration 1: loss = 1.175023
Iteration 2: loss = 1.549872
Iteration 3: loss = 1.073686
Iteration 4: loss = 0.983418
Iteration 5: loss = 0.944507
Iteration 6: loss = 0.947069
Iteration 7: loss = 0.984074
Iteration 8: loss = 0.915022
Iteration 9: loss = 0.952712
Iteration 10: loss = 0.905255
Iteration 11: loss = 0.836812
Iteration 12: loss = 0.815840
Iteration 13: loss = 0.929194
Iteration 14: loss = 0.808420
Iteration 15: loss = 0.810959
Iteration 16: loss = 0.810777
Iteration 17: loss = 0.802796
Iteration 18: loss = 0.824576
Iteration 19: loss = 0.802653
Iteration 20: loss = 0.803866
Iteration 21: loss = 0.789775
Iteration 22: loss = 0.777927
Iteration 23: loss = 0.817194
Iteration 24: loss = 0.816546
Iteration 25: loss = 0.760407
Iteration 26: loss = 0.770471
Iteration 27: loss = 0.758611
Iteration 28: loss = 0.768191
Iteration 29: loss = 0.749339
Iteration 30: loss = 0.759574
Iteration 31: loss = 0.771913
Iteration 32: loss = 0.757703
Iteration 33: loss =

/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [20]:
wandb.init(project="WineQT MLP Classification for all the combinations")
activations = ["sigmoid", "tanh", "relu"]
optimizer = ["SGD","Batch","MiniBatch"]
for i in activations:
    for j in optimizer:
        np.random.seed(27)
        mlp_sgd = Neural_Network(learning_rate=0.01,epochs=5000, inputLayerSize=12, hiddenLayerSize=[18], outputLayerSize=6)
        mlp_sgd.set_activation_function(i)
        mlp_sgd.set_optimizer(j)
        loss = mlp_sgd.train(X_train, y_train)
        y_pred = mlp_sgd.predict(X_val)
        acc = accuracy_score(y_val, y_pred)
        f1 = f1_score(y_val, y_pred, average='macro') 
        precision = precision_score(y_val, y_pred, average='macro')
        recall = recall_score(y_val, y_pred, average='macro')
        wandb.log({"Loss": loss, "Accuracy": acc, "F1 Score": f1, "Precision": precision, "Recall": recall, "label": i})
# print(acc)
# print(train_accuracy)
# wandb.log({"Loss": loss, "Accuracy": acc})
# wandb.log({"Loss": loss, "Accuracy": train_accuracy})



/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Iteration 0: loss = 1.079471
Iteration 1: loss = 1.017345
Iteration 2: loss = 0.996768
Iteration 3: loss = 0.971311
Iteration 4: loss = 0.953751
Iteration 5: loss = 0.952601
Iteration 6: loss = 0.933885
Iteration 7: loss = 0.937233
Iteration 8: loss = 0.920424
Iteration 9: loss = 0.912607
Iteration 10: loss = 0.904023
Iteration 11: loss = 0.900378
Iteration 12: loss = 0.886013
Iteration 13: loss = 0.881356
Iteration 14: loss = 0.878079
Iteration 15: loss = 0.873226
Iteration 16: loss = 0.868015
Iteration 17: loss = 0.868044
Iteration 18: loss = 0.859480
Iteration 19: loss = 0.866585
Iteration 20: loss = 0.859160
Iteration 21: loss = 0.849584
Iteration 22: loss = 0.849462
Iteration 23: loss = 0.844073
Iteration 24: loss = 0.838501
Iteration 25: loss = 0.835475
Iteration 26: loss = 0.836968
Iteration 27: loss = 0.826308
Iteration 28: loss = 0.823571
Iteration 29: loss = 0.820875
Iteration 30: loss = 0.821529
Iteration 31: loss = 0.820916
Iteration 32: loss = 0.820036
Iteration 33: loss =

/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Iteration 0: loss = 2.077601
Iteration 1: loss = 1.175023
Iteration 2: loss = 1.549872
Iteration 3: loss = 1.073686
Iteration 4: loss = 0.983418
Iteration 5: loss = 0.944507
Iteration 6: loss = 0.947069
Iteration 7: loss = 0.984074
Iteration 8: loss = 0.915022
Iteration 9: loss = 0.952712
Iteration 10: loss = 0.905255
Iteration 11: loss = 0.836812
Iteration 12: loss = 0.815840
Iteration 13: loss = 0.929194
Iteration 14: loss = 0.808420
Iteration 15: loss = 0.810959
Iteration 16: loss = 0.810777
Iteration 17: loss = 0.802796
Iteration 18: loss = 0.824576
Iteration 19: loss = 0.802653
Iteration 20: loss = 0.803866
Iteration 21: loss = 0.789775
Iteration 22: loss = 0.777927
Iteration 23: loss = 0.817194
Iteration 24: loss = 0.816546
Iteration 25: loss = 0.760407
Iteration 26: loss = 0.770471
Iteration 27: loss = 0.758611
Iteration 28: loss = 0.768191
Iteration 29: loss = 0.749339
Iteration 30: loss = 0.759574
Iteration 31: loss = 0.771913
Iteration 32: loss = 0.757703
Iteration 33: loss =

/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [21]:

# Define the sweep configuration
sweep_config = {
    "name": "example_sweep",
    "method": "grid",  # Other options: "grid", "bayes"
    "metric": {"goal": "maximize", "name": "accuracy"},
    "parameters": {
        "activation": {"values": ["sigmoid", "tanh", "relu"]},
        "optimizer": {"values": ["SGD", "Batch", "MiniBatch"]},
    },
    "early_terminate": {
        "type": "hyperband",
        "s": 2,
        "eta": 3,
        "max_iter": 27,
    },
}

# Initialize the sweep
sweep_id = wandb.sweep(sweep_config, project="your_project_name")

# Define your training function
def train():
    # Access sweep configuration
    wandb.init(project="your_project_name")
    
    config = wandb.config

    # Your training code here, using hyperparameters from config
    # Example:
    activation = config.activation
    optimizer = config.optimizer

    # Log metrics
    np.random.seed(27)
    mlp_sgd = Neural_Network(learning_rate=0.01,epochs=5000, inputLayerSize=12, hiddenLayerSize=[18], outputLayerSize=6)
    mlp_sgd.set_activation_function(activation)
    mlp_sgd.set_optimizer(optimizer)
    loss = mlp_sgd.train(X_train, y_train)
    y_pred = mlp_sgd.predict(X_val)
    acc = accuracy_score(y_val, y_pred)
    f1 = f1_score(y_val, y_pred, average='macro') 
    precision = precision_score(y_val, y_pred, average='macro')
    recall = recall_score(y_val, y_pred, average='macro')
    wandb.log({"activation": activation, "optimizer": optimizer, "accuracy": acc})

# Start the sweep
wandb.agent(sweep_id, function=train)


wandb: WARNING Calling wandb.login() after wandb.init() has no effect.


Create sweep with ID: 1nygvnda
Sweep URL: https://wandb.ai/mourya/your_project_name/sweeps/1nygvnda


wandb: Agent Starting Run: 4nuzfuhy with config:
wandb: 	activation: sigmoid
wandb: 	optimizer: SGD


<IPython.core.display.HTML object>
<IPython.core.display.HTML object>
<IPython.core.display.HTML object>
<IPython.core.display.HTML object>


wandb: WARNING Ignored wandb.init() arg project when running a sweep.


...

wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: 8kiia0ep with config:
wandb: 	activation: relu
wandb: 	optimizer: Batch
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


wandb: Agent Starting Run: 3v6y35oz with config:
wandb: 	activation: relu
wandb: 	optimizer: MiniBatch
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


Iteration 0: loss = 2.077601
Iteration 1: loss = 1.175023
Iteration 2: loss = 1.549872
Iteration 3: loss = 1.073686
Iteration 4: loss = 0.983418
Iteration 5: loss = 0.944507
Iteration 6: loss = 0.947069
Iteration 7: loss = 0.984074
Iteration 8: loss = 0.915022
Iteration 9: loss = 0.952712
Iteration 10: loss = 0.905255
Iteration 11: loss = 0.836812
Iteration 12: loss = 0.815840
Iteration 13: loss = 0.929194
Iteration 14: loss = 0.808420
Iteration 15: loss = 0.810959
Iteration 16: loss = 0.810777
Iteration 17: loss = 0.802796
Iteration 18: loss = 0.824576
Iteration 19: loss = 0.802653
Iteration 20: loss = 0.803866
Iteration 21: loss = 0.789775
Iteration 22: loss = 0.777927
Iteration 23: loss = 0.817194
Iteration 24: loss = 0.816546
Iteration 25: loss = 0.760407
Iteration 26: loss = 0.770471
Iteration 27: loss = 0.758611
Iteration 28: loss = 0.768191
Iteration 29: loss = 0.749339
Iteration 30: loss = 0.759574
Iteration 31: loss = 0.771913
Iteration 32: loss = 0.757703
Iteration 33: loss =

/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


wandb: Sweep Agent: Waiting for job.
wandb: Sweep Agent: Exiting.


In [22]:
activation = ["sigmoid", "tanh", "relu"]
optimizer = ["SGD", "Batch", "MiniBatch"]
learning_rates = [0.1,0.01,0.001,0.0001]
epochs = [100,500,1000]
hiddenlayersize = [[14], [16], [18], [20], [18,18]]
results = []
hyperparameters = []
for i in activation:
    for j in optimizer:
        for k in learning_rates:
            for l in epochs:
                for m in hiddenlayersize:
                    mlp_sgd = Neural_Network(learning_rate=0.01,epochs=5000, inputLayerSize=12, hiddenLayerSize=[18], outputLayerSize=6)
                    mlp_sgd.set_activation_function(i)
                    mlp_sgd.set_optimizer(j)
                    mlp_sgd.set_learning_rate(k)
                    # print(l)
                    mlp_sgd.max_iterations = l;
                    # print(mlp_sgd.max_iterations)
                    # mlp_sgd.set_epochs(l)
                    # print(mlp_sgd.max_iterations)
                    mlp_sgd.set_hidden_layers(m)
                    # print(mlp_sgd.max_iterations)
                    loss = mlp_sgd.train(X_train, y_train)
                    y_pred = mlp_sgd.predict(X_val)
                    acc = accuracy_score(y_val, y_pred)
                    f1 = f1_score(y_val, y_pred, average='macro') 
                    precision = precision_score(y_val, y_pred, average='macro')
                    recall = recall_score(y_val, y_pred, average='macro')
                    print(acc, [i,j,k,l,m])
                    results.append([acc, f1, precision, recall])
                    hyperparameters.append([i, j, k, l, m])
result_df = pd.DataFrame(results, columns=['Accuracy', 'F1 Score', 'Precision', 'Recall'])
result_df['Activation'] = [param[0] for param in hyperparameters]
result_df['Optimizer'] = [param[1] for param in hyperparameters]
result_df['Learning Rate'] = [param[2] for param in hyperparameters]
result_df['Epochs'] = [param[3] for param in hyperparameters]
result_df['Hidden Layer Size'] = [param[4] for param in hyperparameters]

# Find the hyperparameter combination with the highest accuracy
best_hyperparameters = result_df.loc[result_df['Accuracy'].idxmax()]

# Print the best hyperparameter combination and its corresponding metrics
print("Best Hyperparameters:")
print(best_hyperparameters)

# Print the results table
print("\nResults Table:")
print(result_df)            
                    


/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics

0.5414847161572053 ['sigmoid', 'SGD', 0.1, 100, [14]]
0.5633187772925764 ['sigmoid', 'SGD', 0.1, 100, [16]]
0.4279475982532751 ['sigmoid', 'SGD', 0.1, 100, [18]]
0.519650655021834 ['sigmoid', 'SGD', 0.1, 100, [20]]
0.5327510917030568 ['sigmoid', 'SGD', 0.1, 100, [18, 18]]
0.5938864628820961 ['sigmoid', 'SGD', 0.1, 500, [14]]
0.5633187772925764 ['sigmoid', 'SGD', 0.1, 500, [16]]
0.5283842794759825 ['sigmoid', 'SGD', 0.1, 500, [18]]
0.5720524017467249 ['sigmoid', 'SGD', 0.1, 500, [20]]
0.5458515283842795 ['sigmoid', 'SGD', 0.1, 500, [18, 18]]
0.611353711790393 ['sigmoid', 'SGD', 0.1, 1000, [14]]


/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics

0.5589519650655022 ['sigmoid', 'SGD', 0.1, 1000, [16]]
0.5982532751091703 ['sigmoid', 'SGD', 0.1, 1000, [18]]
0.6506550218340611 ['sigmoid', 'SGD', 0.1, 1000, [20]]
0.537117903930131 ['sigmoid', 'SGD', 0.1, 1000, [18, 18]]
0.5109170305676856 ['sigmoid', 'SGD', 0.01, 100, [14]]
0.5327510917030568 ['sigmoid', 'SGD', 0.01, 100, [16]]
0.4978165938864629 ['sigmoid', 'SGD', 0.01, 100, [18]]
0.537117903930131 ['sigmoid', 'SGD', 0.01, 100, [20]]
0.519650655021834 ['sigmoid', 'SGD', 0.01, 100, [18, 18]]
0.6244541484716157 ['sigmoid', 'SGD', 0.01, 500, [14]]


/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics

...

/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Iteration 110: loss = 0.451506
Iteration 111: loss = 0.496760
Iteration 112: loss = 0.529722
Iteration 113: loss = 0.458338
Iteration 114: loss = 0.482748
Iteration 115: loss = 0.458218
Iteration 116: loss = 0.605147
Iteration 117: loss = 0.484615
Iteration 118: loss = 0.483461
Iteration 119: loss = 0.481430
Iteration 120: loss = 0.508341
Iteration 121: loss = 0.479689
Iteration 122: loss = 0.439285
Iteration 123: loss = 0.469431
Iteration 124: loss = 0.431284
Iteration 125: loss = 0.479221
Iteration 126: loss = 0.478730
Iteration 127: loss = 0.472748
Iteration 128: loss = 0.443765
Iteration 129: loss = 0.444321
Iteration 130: loss = 0.468148
Iteration 131: loss = 0.462576
Iteration 132: loss = 0.417881
Iteration 133: loss = 0.517877
Iteration 134: loss = 0.732693
Iteration 135: loss = 0.535448
Iteration 136: loss = 0.646812
Iteration 137: loss = 0.505945
Iteration 138: loss = 0.415559
Iteration 139: loss = 0.429939
Iteration 140: loss = 0.449555
Iteration 141: loss = 0.402864
Iteratio

/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Iteration 127: loss = 0.540976
Iteration 128: loss = 0.545665
Iteration 129: loss = 0.476201
Iteration 130: loss = 0.470315
Iteration 131: loss = 0.443470
Iteration 132: loss = 0.501148
Iteration 133: loss = 0.456747
Iteration 134: loss = 0.479320
Iteration 135: loss = 0.447693
Iteration 136: loss = 0.452375
Iteration 137: loss = 0.466456
Iteration 138: loss = 0.509034
Iteration 139: loss = 0.480841
Iteration 140: loss = 0.565569
Iteration 141: loss = 0.465909
Iteration 142: loss = 0.458889
Iteration 143: loss = 0.469456
Iteration 144: loss = 0.445262
Iteration 145: loss = 0.535706
Iteration 146: loss = 0.510511
Iteration 147: loss = 0.532949
Iteration 148: loss = 0.507908
Iteration 149: loss = 0.451385
Iteration 150: loss = 0.474945
Iteration 151: loss = 0.452074
Iteration 152: loss = 0.436742
Iteration 153: loss = 0.532040
Iteration 154: loss = 0.497163
Iteration 155: loss = 0.646181
Iteration 156: loss = 0.457081
Iteration 157: loss = 0.459328
Iteration 158: loss = 0.418367
Iteratio

/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [23]:
np.random.seed(41)
mlp_sgd = Neural_Network(learning_rate=0.01,epochs=5000, inputLayerSize=12, hiddenLayerSize=[18], outputLayerSize=6)
mlp_sgd.set_activation_function('relu')
mlp_sgd.set_optimizer('Batch')
mlp_sgd.set_learning_rate(0.01)
# print(l)
mlp_sgd.max_iterations = 500;
mlp_sgd.set_hidden_layers([18])
loss = mlp_sgd.train(X_train, y_train)
y_pred = mlp_sgd.predict(X_test)
acc = accuracy_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred, average='macro') 
precision = precision_score(y_test, y_pred, average='macro')
recall = recall_score(y_test, y_pred, average='macro')
print(acc, loss)

0.4017467248908297 0.909663045591907


/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


###### 

In [2]:
class MultilabelMLP(object):
    def __init__(self, learning_rate=0.01,epochs = 5000, inputLayerSize: int = 2, hiddenLayerSize = [3,3,3] , outputLayerSize: int = 1):
        # Define Hyperparameters
        self.inputLayerSize = inputLayerSize
        self.outputLayerSize = outputLayerSize
        self.hiddenLayerSize = hiddenLayerSize
        self.activation = self.relu
        self.activationPrime = self.reluPrime
        self.learning_rate = learning_rate
        # Weights (parameters)
        self.num_layers = len(hiddenLayerSize)+1
        self.weights = []
        self.weights.append(np.random.randn(self.inputLayerSize, self.hiddenLayerSize[0]))
        for i in range(1,self.num_layers-1):
            self.weights.append(np.random.randn(self.hiddenLayerSize[i-1], self.hiddenLayerSize[i]))
        self.weights.append(np.random.randn(self.hiddenLayerSize[-1], self.outputLayerSize))
        self.optimizer = 'SGD'
        self.max_iterations = epochs

    def forward(self, X):
        self.z = [None] * (len(self.weights))
        self.a = [None] * (len(self.weights)-1)
        
        self.z[0] = np.dot(X, self.weights[0])
        for i in range(0,len(self.a)):
            self.a[i] = self.activation(self.z[i])
            self.z[i+1] = np.dot(self.a[i],self.weights[i+1])
        yHat = self.softmax(self.z[-1])
        return yHat

    def relu(self, z):
        return np.maximum(0, z)  # ReLU activation

    def tanh(self, z):
        return np.tanh(z)  # Tanh activation

    def sigmoid(self, z):
        return 1 / (1 + np.exp(-z))

    def sigmoidPrime(self, z):
        return np.exp(-z) / ((1 + np.exp(-z))**2)

    def softmax(self, z):
        exp_z = np.exp(z - np.max(z))  # Subtracting max(z) for numerical stability
        return exp_z / exp_z.sum(axis=1, keepdims=True)

    def costFunction(self, X, y):
        self.yHat = self.forward(X)
        J = -np.sum(y * np.log(self.yHat)) / len(X)
        return J

    def costFunctionPrime(self, X, y):
        self.yHat = self.forward(X)
        deltas = [None] * (len(self.weights))
        deltas[-1] = self.yHat - y
        dJdWs = [None] * (len(self.weights))
        for i in range(len(deltas)-2,-1,-1):
            dJdWs[i+1] = np.dot(self.a[i].T, deltas[i+1])
            deltas[i] = np.dot(deltas[i+1],self.weights[i+1].T)*self.activationPrime(self.z[i])
        dJdWs[0] = np.dot(X.T, deltas[0])
        
        # delta3 = self.yHat - y
        # dJdW2 = np.dot(self.a2.T, delta3)

        # delta2 = np.dot(delta3, self.W2.T) * self.activationPrime(self.z2)  # Use ReLU derivative
        # dJdW1 = np.dot(X.T, delta2)

        return dJdWs

    def reluPrime(self, z):
        return np.where(z > 0, 1, 0)  # Derivative of ReLU

    def tanhPrime(self, z):
        return 1 - np.tanh(z)**2  # Derivative of Tanh

    def backward(self, X, y, learning_rate):
        dJdWs = self.costFunctionPrime(X, y)
        for i in range(len(self.weights)):
            self.weights[i] -= learning_rate * dJdWs[i]
        # self.W1 -= learning_rate * dJdW1
        # self.W2 -= learning_rate * dJdW2
    def train(self, X, y, batch_size = 32, learning_rate=0.1, max_iterations=10000):
        if(self.optimizer == 'SGD'):
            return self.train_sgd(X=X, y=y)
        elif(self.optimizer == 'Batch'):
            return self.train_batch(X=X, y=y)
        elif(self.optimizer == 'MiniBatch'):
            return self.train_mini_batch(X=X, y=y)
    def train_sgd(self, X, y, learning_rate=0.1, max_iterations=1000):
        for i in range(self.max_iterations):
            idx = np.random.randint(len(X))
            self.backward(X[idx:idx+1], y[idx:idx+1], learning_rate)
            # if i % 1000 == 0:
            #     loss = self.costFunction(X, y)
            #     print("Iteration %d: loss = %f" % (i, loss))
        loss = self.costFunction(X, y)
        return loss
        print("Training completed.")
    def train_batch(self, X, y, learning_rate=0.0001, max_iterations=1000):
        for i in range(self.max_iterations):
            self.backward(X, y, learning_rate)
            # if i % 1000 == 0:
            #     loss = self.costFunction(X, y)
            #     print("Iteration %d: loss = %f" % (i, loss))
        loss = self.costFunction(X, y)
        return loss
        print("Training completed.")
    def train_mini_batch(self, X, y, batch_size=32, learning_rate=0.01, max_iterations=1000):
        for i in range(self.max_iterations):
            # Randomly shuffle the data and split into mini-batches
            indices = np.arange(len(X))
            np.random.shuffle(indices)
            for j in range(0, len(X), batch_size):
                batch_indices = indices[j:j+batch_size]
                self.backward(X[batch_indices], y[batch_indices], learning_rate)
            # if i % 1 == 0:
            #     loss = self.costFunction(X, y)
            #     print("Iteration %d: loss = %f" % (i, loss))
        loss = self.costFunction(X, y)
        return loss
        print("Training completed.")

    def predict(self, X, y):
        yHat = self.forward(X)
        # print(X)
        # print(y)
        # print(yHat)
        # binary_predictions = []
        # for i in range(len(y)):
        #     count = np.sum(y[i] > 0)
        #     print(count)
        #     yHat[i] = yHat[i]*count
        #     temp = (yHat[i] > 0.5).astype(int)
        #     lis = temp/np.sum(temp)
        #     lis = lis.tolist()
        #     binary_predictions.append(lis)
        # return np.array(binary_predictions)
        binary_predictions = (yHat > 0.2).astype(int)
        return np.array(binary_predictions)
        # return np.argmax(yHat, axis=1)
    def set_learning_rate(self, learning_rate):
        self.learning_rate = learning_rate

    def set_activation_function(self, activation_function):
        if(activation_function == 'sigmoid'):
            self.activation = self.sigmoid
            self.activationPrime = self.sigmoidPrime
        if(activation_function == 'relu'):
            self.activation = self.relu
            self.activationPrime = self.reluPrime
        if(activation_function == 'tanh'):
            self.activation = self.tanh
            self.activationPrime = self.tanhPrime

    def set_optimizer(self, optimizer):
        self.optimizer = optimizer

    def set_hidden_layers(self, hidden_layer_sizes):
        self.hiddenLayerSize = hidden_layer_sizes
        self.num_layers = len(self.hiddenLayerSize)+1
        self.weights = []
        self.weights.append(np.random.randn(self.inputLayerSize, self.hiddenLayerSize[0]))
        for i in range(1,self.num_layers-1):
            self.weights.append(np.random.randn(self.hiddenLayerSize[i-1], self.hiddenLayerSize[i]))
        self.weights.append(np.random.randn(self.hiddenLayerSize[-1], self.outputLayerSize))
        # self.W1 = np.random.randn(self.inputLayerSize, self.hiddenLayerSize)
        # self.W2 = np.random.randn(self.hiddenLayerSize, self.outputLayerSize)
        # self.weights, self.biases = self.initialize_weights()
    def set_epochs(self, epcohs):
        self.max_iterations = epochs
        print(self.max_iterations)


In [3]:

scaler = StandardScaler()
minmax_scaler = MinMaxScaler()
data = pd.read_csv('advertisement.csv')
data.fillna(method='ffill', inplace=True) 
categorical_cols = ['gender', 'education', 'married', 'city', 'occupation', 'most bought item']
data_encoded = pd.get_dummies(data, columns=categorical_cols, drop_first=True)
X = data_encoded.drop('labels', axis=1)  # Features
y = data_encoded['labels']  # Target variable
X = scaler.fit_transform(X)
mlb = MultiLabelBinarizer()
y = mlb.fit_transform(y.str.split(' '))
# print(y)
y_fin = []
for i in range(len(y)):
    # print(y[i])
    # print(np.sum(y[i]))
    x = y[i]/np.sum(y[i])
    y_fin.append(x)
y = y_fin
y = np.array(y)
print(y)
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.4, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X, y, test_size=0.5, random_state=42)
print(X_train.shape)
print(y_train.shape)

[[0.         0.         0.33333333 ... 0.         0.         0.33333333]
 [0.5        0.         0.         ... 0.5        0.         0.        ]
 [0.         0.         0.25       ... 0.         0.         0.25      ]
 ...
 [0.         0.         0.5        ... 0.         0.         0.5       ]
 [1.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.5        0.5        ... 0.         0.         0.        ]]
(600, 1010)
(600, 8)


In [4]:
mask = (y_val > 0)
y_val[mask] = 1
print(y_val)

[[0. 0. 1. ... 0. 0. 0.]
 [0. 0. 0. ... 1. 0. 0.]
 [0. 0. 0. ... 1. 0. 0.]
 ...
 [1. 0. 0. ... 0. 1. 1.]
 [0. 0. 0. ... 1. 0. 0.]
 [1. 1. 0. ... 0. 0. 0.]]


In [39]:
np.random.seed(0)
mlp_sgd = MultilabelMLP(inputLayerSize=1010, hiddenLayerSize=[1000], outputLayerSize=8)
mlp_sgd.set_activation_function('sigmoid')
loss = mlp_sgd.train_sgd(X_train, y_train)
y_pred = mlp_sgd.predict(X_val, y_train)
cnt = 0
for i in range(len(y_pred)):
    for j in range(len(y_pred[0])):
        if((y_pred[i][j] > 0 and y_val[i][j] == 0) or (y_pred[i][j] == 0 and y_val[i][j] > 0)):
            cnt += 1
print("Loss:", loss)
print("Accuracy:", 1-hamming_loss(y_val,y_pred))
print("F1 Score", f1_score(y_val,y_pred, average='macro'))
print("Precision", precision_score(y_val,y_pred, average='macro'))
print("Recall", recall_score(y_val,y_pred, average='macro'))
print(cnt)
print(len(y_pred)*len(y_pred[0]))

Loss: 13.914022483562807
Accuracy: 0.75075
F1 Score 0.4526455953468639
Precision 0.9545214404846567
Recall 0.33399342062024456
997
4000


In [40]:
print(y_train)
y_temp = copy(y_train)
mask = (y_temp > 0)
y_temp[mask] = 1
# print(y_train)
y_train_pred = mlp_sgd.predict(X_train, y_temp)
cnt = 0
for i in range(len(y_train_pred)):
    for j in range(len(y_train_pred[0])):
        if((y_train_pred[i][j] > 0 and y_temp[i][j] == 0) or (y_train_pred[i][j] == 0 and y_temp[i][j] > 0)):
            cnt += 1
print("Loss:", loss)
# print(y_train)
# print(y_train_pred)
print("Accuracy:", 1-hamming_loss(y_temp,y_train_pred))
print("F1 Score", f1_score(y_temp,y_train_pred, average='macro'))
print("Precision", precision_score(y_temp,y_train_pred, average='macro'))
print("Recall", recall_score(y_temp,y_train_pred, average='macro'))
print(cnt)
print(len(y_train_pred)*len(y_train_pred[0]))
print(y_train)

[[0.         0.5        0.         ... 0.         0.         0.        ]
 [0.         0.         0.33333333 ... 0.         0.         0.        ]
 [0.25       0.         0.25       ... 0.         0.         0.        ]
 ...
 [0.25       0.         0.         ... 0.         0.25       0.25      ]
 [0.         0.         0.         ... 0.5        0.         0.        ]
 [0.5        0.5        0.         ... 0.         0.         0.        ]]
Loss: 13.914022483562807
Accuracy: 0.7529166666666667
F1 Score 0.45327611347673413
Precision 0.9521754422442301
Recall 0.3352920732677347
1186
4800
[[0.         0.5        0.         ... 0.         0.         0.        ]
 [0.         0.         0.33333333 ... 0.         0.         0.        ]
 [0.25       0.         0.25       ... 0.         0.         0.        ]
 ...
 [0.25       0.         0.         ... 0.         0.25       0.25      ]
 [0.         0.         0.         ... 0.5        0.         0.        ]
 [0.5        0.5        0.         ...

In [54]:
activations = ["sigmoid", "tanh", "relu"]
optimizer = ["SGD","Batch","MiniBatch"]
for i in activations:
    for j in optimizer:
        np.random.seed(27)
        mlp_sgd = MultilabelMLP(inputLayerSize=1010, hiddenLayerSize=[1000], outputLayerSize=8)
        mlp_sgd.set_activation_function(i)
        mlp_sgd.set_optimizer(j)
        mlp_sgd.max_iterations = 100
        loss = mlp_sgd.train(X_train, y_train)
        y_pred = mlp_sgd.predict(X_val, y_train)
        print("Parameters: ", i, j)
        acc = 1-hamming_loss(y_val, y_pred)
        f1 = f1_score(y_val, y_pred, average='macro') 
        precision = precision_score(y_val, y_pred, average='macro')
        recall = recall_score(y_val, y_pred, average='macro')
        print("Accuracy: ", acc, "F1 Score:", f1, "Precision:", precision, "Recall:", recall)
        

Parameters:  sigmoid SGD
Accuracy:  0.6267499999999999 F1 Score: 0.2212114477101492 Precision: 0.41572170959080773 Recall: 0.17087652203711667


/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Parameters:  sigmoid Batch
Accuracy:  0.70425 F1 Score: 0.5020784900403972 Precision: 0.6298582793005906 Recall: 0.418229496179073
Parameters:  sigmoid MiniBatch
Accuracy:  0.7965 F1 Score: 0.5541993249212752 Precision: 1.0 Recall: 0.441501660217273
Parameters:  tanh SGD
Accuracy:  0.63575 F1 Score: 0.2551722827961064 Precision: 0.47419478547037053 Recall: 0.17525012898449246
Parameters:  tanh Batch
Accuracy:  0.7755 F1 Score: 0.6348793839460656 Precision: 0.7598762848915304 Recall: 0.5468124532797851
Parameters:  tanh MiniBatch
Accuracy:  0.81925 F1 Score: 0.661279271964512 Precision: 1.0 Recall: 0.4949737411081802


/tmp/ipykernel_329209/3232201098.py:45: RuntimeWarning: invalid value encountered in divide
  return exp_z / exp_z.sum(axis=1, keepdims=True)
/tmp/ipykernel_329209/3232201098.py:49: RuntimeWarning: divide by zero encountered in log
  J = -np.sum(y * np.log(self.yHat)) / len(X)
/tmp/ipykernel_329209/3232201098.py:49: RuntimeWarning: invalid value encountered in multiply
  J = -np.sum(y * np.log(self.yHat)) / len(X)
/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/tmp/ipykernel_329209/3232201098.py:45: RuntimeWarning: invalid value encountered in divide
  return exp_z / exp_z.sum(axis=1, keepdims=True)


Parameters:  relu SGD
Accuracy:  0.64225 F1 Score: 0.0014880952380952382 Precision: 0.125 Recall: 0.0007485029940119761
Parameters:  relu Batch
Accuracy:  0.642 F1 Score: 0.0 Precision: 0.0 Recall: 0.0


/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/tmp/ipykernel_329209/3232201098.py:45: RuntimeWarning: invalid value encountered in divide
  return exp_z / exp_z.sum(axis=1, keepdims=True)


Parameters:  relu MiniBatch
Accuracy:  0.642 F1 Score: 0.0 Precision: 0.0 Recall: 0.0


/home/ubuntulsa/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [6]:
# activation = ["sigmoid", "tanh", "relu"]
# optimizer = ["SGD", "Batch", "MiniBatch"]
activation = ["sigmoid"]
optimizer = ["MiniBatch"]
learning_rates = [0.1,0.01,0.001,0.0001]
epochs = [10,50,100]
hiddenlayersize = [[100,100], [100], [500], [1000], [1000,1000]]
results = []
hyperparameters = []
for i in activation:
    for j in optimizer:
        for k in learning_rates:
            for l in epochs:
                for m in hiddenlayersize:
                    mlp_sgd = MultilabelMLP(inputLayerSize=1010, hiddenLayerSize=[100], outputLayerSize=8)
                    mlp_sgd.set_activation_function(i)
                    mlp_sgd.set_optimizer(j)
                    mlp_sgd.set_learning_rate(k)
                    # print(l)
                    mlp_sgd.max_iterations = l;
                    # print(mlp_sgd.max_iterations)
                    # mlp_sgd.set_epochs(l)
                    # print(mlp_sgd.max_iterations)
                    mlp_sgd.set_hidden_layers(m)
                    # print(mlp_sgd.max_iterations)
                    loss = mlp_sgd.train(X_train, y_train)
                    y_pred = mlp_sgd.predict(X_val, y_train)
                    acc = 1-hamming_loss(y_val, y_pred)
                    f1 = f1_score(y_val, y_pred, average='macro') 
                    precision = precision_score(y_val, y_pred, average='macro')
                    recall = recall_score(y_val, y_pred, average='macro')
                    print(acc, [i,j,k,l,m])
                    results.append([acc, f1, precision, recall])
                    hyperparameters.append([i, j, k, l, m])
result_df = pd.DataFrame(results, columns=['Accuracy', 'F1 Score', 'Precision', 'Recall'])
result_df['Activation'] = [param[0] for param in hyperparameters]
result_df['Optimizer'] = [param[1] for param in hyperparameters]
result_df['Learning Rate'] = [param[2] for param in hyperparameters]
result_df['Epochs'] = [param[3] for param in hyperparameters]
result_df['Hidden Layer Size'] = [param[4] for param in hyperparameters]

# Find the hyperparameter combination with the highest accuracy
best_hyperparameters = result_df.loc[result_df['Accuracy'].idxmax()]

# Print the best hyperparameter combination and its corresponding metrics
print("Best Hyperparameters:")
print(best_hyperparameters)

# Print the results table
print("\nResults Table:")
print(result_df)            
                    


0.73725 ['sigmoid', 'MiniBatch', 0.1, 10, [100, 100]]
0.706 ['sigmoid', 'MiniBatch', 0.1, 10, [100]]
0.7935 ['sigmoid', 'MiniBatch', 0.1, 10, [500]]
0.759 ['sigmoid', 'MiniBatch', 0.1, 10, [1000]]
0.77825 ['sigmoid', 'MiniBatch', 0.1, 10, [1000, 1000]]
0.88825 ['sigmoid', 'MiniBatch', 0.1, 50, [100, 100]]
0.80175 ['sigmoid', 'MiniBatch', 0.1, 50, [100]]
0.846 ['sigmoid', 'MiniBatch', 0.1, 50, [500]]
0.78725 ['sigmoid', 'MiniBatch', 0.1, 50, [1000]]
0.79525 ['sigmoid', 'MiniBatch', 0.1, 50, [1000, 1000]]
0.92375 ['sigmoid', 'MiniBatch', 0.1, 100, [100, 100]]
0.80625 ['sigmoid', 'MiniBatch', 0.1, 100, [100]]
0.871 ['sigmoid', 'MiniBatch', 0.1, 100, [500]]
0.7905 ['sigmoid', 'MiniBatch', 0.1, 100, [1000]]
0.788 ['sigmoid', 'MiniBatch', 0.1, 100, [1000, 1000]]
0.73925 ['sigmoid', 'MiniBatch', 0.01, 10, [100, 100]]
0.69225 ['sigmoid', 'MiniBatch', 0.01, 10, [100]]
0.78975 ['sigmoid', 'MiniBatch', 0.01, 10, [500]]
0.76925 ['sigmoid', 'MiniBatch', 0.01, 10, [1000]]
0.76225 ['sigmoid', 'MiniBa

In [7]:
np.random.seed(0)
mlp_sgd = MultilabelMLP(inputLayerSize=1010, hiddenLayerSize=[1000], outputLayerSize=8)
mlp_sgd.set_activation_function('sigmoid')
loss = mlp_sgd.train_sgd(X_train, y_train)
y_pred = mlp_sgd.predict(X_test, y_train)
mask = (y_test > 0)
y_test[mask] = 1
print(y_test)
cnt = 0
for i in range(len(y_pred)):
    for j in range(len(y_pred[0])):
        if((y_pred[i][j] > 0 and y_test[i][j] == 0) or (y_pred[i][j] == 0 and y_test[i][j] > 0)):
            cnt += 1
print("Loss:", loss)
print("Accuracy:", 1-hamming_loss(y_test,y_pred))
print("F1 Score", f1_score(y_test,y_pred, average='macro'))
print("Precision", precision_score(y_test,y_pred, average='macro'))
print("Recall", recall_score(y_test,y_pred, average='macro'))
print(cnt)
print(len(y_pred)*len(y_pred[0]))

[[1. 1. 0. ... 1. 0. 0.]
 [0. 1. 0. ... 1. 0. 0.]
 [1. 1. 0. ... 0. 1. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [1. 0. 0. ... 0. 0. 0.]
 [1. 1. 1. ... 0. 0. 1.]]
Loss: 13.914022483562807
Accuracy: 0.6655
F1 Score 0.24086030577394757
Precision 0.537998382998383
Recall 0.1972212322059035
1338
4000
